In [2]:
import pandas as pd
import numpy as np
from sklearn.decomposition import TruncatedSVD
from scipy.stats import pearsonr
from sklearn.metrics.pairwise import cosine_similarity

In [3]:
movie_ratings = pd.read_csv('./dataset/ratings.csv')
movie_ratings_small = pd.read_csv('./dataset/ratings_small.csv')
credits = pd.read_csv('./dataset/credits.csv')
links = pd.read_csv('./dataset/links.csv')
links_small = pd.read_csv('./dataset/links_small.csv')
movies_metadata = pd.read_csv('./dataset/movies_metadata.csv')
keywords = pd.read_csv('./dataset/keywords.csv')

/var/folders/s7/_6xph2kx7zj1t3c3tmb0gk5c0000gn/T/ipykernel_5451/983951038.py:6: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  movies_metadata = pd.read_csv('./dataset/movies_metadata.csv')


In [4]:
movie_ratings.head()

userId  movieId  rating   timestamp
0       1      110     1.0  1425941529
1       1      147     4.5  1425942435
2       1      858     5.0  1425941523
3       1     1221     5.0  1425941546
4       1     1246     5.0  1425941556

In [5]:
movie_ratings_small.head()

userId  movieId  rating   timestamp
0       1       31     2.5  1260759144
1       1     1029     3.0  1260759179
2       1     1061     3.0  1260759182
3       1     1129     2.0  1260759185
4       1     1172     4.0  1260759205

In [6]:
movie_ratings.shape, movie_ratings_small.shape

((26024289, 4), (100004, 4))

In [7]:
movies_metadata = movies_metadata.drop_duplicates(subset='id', keep='first')

In [8]:
movies_metadata = movies_metadata[movies_metadata['id'].str.isdigit()]
movies_metadata['id'] = movies_metadata['id'].astype('int64')

In [9]:
# 두 데이터프레임 병합 (movieId 기준)
movies_metadata = movies_metadata.merge(movie_ratings,
                                        left_on='id',
                                        right_on='movieId',
                                        how='left')

# 필요 없어진 movieId 열 제거
movies_metadata = movies_metadata.drop(columns=['movieId'])


In [10]:
movies_metadata.head()

adult                              belongs_to_collection    budget  \
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
2  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
3  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
4  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
1  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
2  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
3  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
4  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   

                               homepage   id    imdb_id original_language  \
0  http://toystory.disney.com/toy-story  862  tt0114709                en   
1  http://toystory.disney.com/toy-story  862  tt0114709                en   
2  http://toystory.disney.com/toy-story  862  tt0114709                en   
3  http://toystory.disney.com/toy-story  862  tt0114709                en   
4  http://toystory.disney.com/toy-story  862  tt0114709                en   

  original_title                                           overview  ...  \
0      Toy Story  Led by Woody, Andy's toys live happily in his ...  ...   
1      Toy Story  Led by Woody, Andy's toys live happily in his ...  ...   
2      Toy Story  Led by Woody, Andy's toys live happily in his ...  ...   
3      Toy Story  Led by Woody, Andy's toys live happily in his ...  ...   
4      Toy Story  Led by Woody, Andy's toys live happily in his ...  ...   

                           spoken_languages    status tagline      title  \
0  [{'iso_639_1': 'en', 'name': 'English'}]  Released     NaN  Toy Story   
1  [{'iso_639_1': 'en', 'name': 'English'}]  Released     NaN  Toy Story   
2  [{'iso_639_1': 'en', 'name': 'English'}]  Released     NaN  Toy Story   
3  [{'iso_639_1': 'en', 'name': 'English'}]  Released     NaN  Toy Story   
4  [{'iso_639_1': 'en', 'name': 'English'}]  Released     NaN  Toy Story   

   video  vote_average  vote_count  userId rating    timestamp  
0  False           7.7      5415.0  1923.0    3.0  858335006.0  
1  False           7.7      5415.0  2103.0    5.0  946044912.0  
2  False           7.7      5415.0  5380.0    1.0  878941641.0  
3  False           7.7      5415.0  6177.0    4.0  859415226.0  
4  False           7.7      5415.0  6525.0    4.0  857388995.0  

[5 rows x 27 columns]

In [11]:
a = movies_metadata[['id','original_title','userId', 'rating']]
a.head()

id original_title  userId  rating
0  862      Toy Story  1923.0     3.0
1  862      Toy Story  2103.0     5.0
2  862      Toy Story  5380.0     1.0
3  862      Toy Story  6177.0     4.0
4  862      Toy Story  6525.0     4.0

In [12]:
movies_metadata = movies_metadata.dropna(subset=['userId'], axis = 0)

In [13]:
a.head()

id original_title  userId  rating
0  862      Toy Story  1923.0     3.0
1  862      Toy Story  2103.0     5.0
2  862      Toy Story  5380.0     1.0
3  862      Toy Story  6177.0     4.0
4  862      Toy Story  6525.0     4.0

In [18]:
user_matrix = pd.pivot_table(a, index="userId", columns='original_title',values='rating',aggfunc="mean", fill_value=0)
user_matrix

original_title  !Women Art Revolution  $5 a Day  'Gator Bait  'R Xmas  \
userId                                                                  
1.0                               0.0       0.0          0.0      0.0   
2.0                               0.0       0.0          0.0      0.0   
3.0                               0.0       0.0          0.0      0.0   
4.0                               0.0       0.0          0.0      0.0   
5.0                               0.0       0.0          0.0      0.0   
...                               ...       ...          ...      ...   
270892.0                          0.0       0.0          0.0      0.0   
270893.0                          0.0       0.0          0.0      0.0   
270894.0                          0.0       0.0          0.0      0.0   
270895.0                          0.0       0.0          0.0      0.0   
270896.0                          0.0       0.0          0.0      0.0   

original_title  'Twas the Night Before Christmas  (A)Sexual  \
userId                                                        
1.0                                          0.0        0.0   
2.0                                          0.0        0.0   
3.0                                          0.0        0.0   
4.0                                          0.0        0.0   
5.0                                          0.0        0.0   
...                                          ...        ...   
270892.0                                     0.0        0.0   
270893.0                                     0.0        0.0   
270894.0                                     0.0        0.0   
270895.0                                     0.0        0.0   
270896.0                                     0.0        0.0   

original_title  ...And the Pursuit of Happiness  ...Più forte ragazzi!  \
userId                                                                   
1.0                                         0.0                    0.0   
2.0                                         0.0                    0.0   
3.0                                         0.0                    0.0   
4.0                                         0.0                    0.0   
5.0                                         0.0                    0.0   
...                                         ...                    ...   
270892.0                                    0.0                    3.5   
270893.0                                    0.0                    0.0   
270894.0                                    0.0                    0.0   
270895.0                                    0.0                    0.0   
270896.0                                    0.0                    4.0   

original_title  ...altrimenti ci arrabbiamo!  \
userId                                         
1.0                                      0.0   
2.0                                      0.0   
3.0                                      0.0   
4.0                                      0.0   
5.0                                      0.0   
...                                      ...   
270892.0                                 0.0   
270893.0                                 0.0   
270894.0                                 0.0   
270895.0                                 0.0   
270896.0                                 0.0   

original_title  00 Schneider - Jagd auf Nihil Baxter  ...  친절한 금자씨   태풍  파란대문  \
userId                                                ...                       
1.0                                              0.0  ...      0.0  0.0   0.0   
2.0                                              0.0  ...      0.0  0.0   0.0   
3.0                                              0.0  ...      0.0  0.0   0.0   
4.0                                              0.0  ...      0.0  0.0   0.0   
5.0                                              0.0  ...      0.0  0.0   0.0   
...                                              ...  ...      ...  ...   .

In [19]:
svd = TruncatedSVD(n_components=50)  # k=50으로 차원 축소
reduced_matrix = svd.fit_transform(user_matrix)

In [22]:
# 피어슨 상관계수 계산
def calculate_pearson_similarity(matrix, user_id):
    target_user_vector = matrix[user_id]
    similarities = {}
    
    for other_user_id in range(matrix.shape[0]):
        if other_user_id != user_id:
            corr, _ = pearsonr(target_user_vector, matrix[other_user_id])
            similarities[other_user_id] = corr
    
    return similarities

# 특정 사용자에 대해 유사도 계산
user_id = 0  # 예: 첫 번째 사용자
similarities = calculate_pearson_similarity(reduced_matrix, user_id)

# 유사도 정렬
sorted_similarities = sorted(similarities.items(), key=lambda x: x[1], reverse=True)
print(sorted_similarities)

[(58296, 0.8492078121559458), (12105, 0.8419382289574815), (11471, 0.8170927799065852), (172909, 0.8143880604563958), (68019, 0.7990195086176071), (145826, 0.7976520485425508), (159241, 0.7848602796442082), (244968, 0.7832570239572612), (199177, 0.7802080137909112), (73993, 0.7797156542759626), (44677, 0.7784866312277096), (147748, 0.7761176103416427), (12320, 0.772238653209523), (183143, 0.7716139527047956), (186708, 0.7704654080475412), (73414, 0.7688912769812989), (66338, 0.7673876152076428), (154346, 0.7673539252853327), (22615, 0.7672831880071523), (6769, 0.7667329961315614), (208099, 0.7664115269905841), (84842, 0.7643901814041285), (152346, 0.7643473468075025), (56043, 0.7643252263962732), (164435, 0.7621900168356779), (120820, 0.7593566220214718), (59657, 0.7566449359692266), (155179, 0.7548271674720135), (216200, 0.7535204373092208), (257919, 0.7532056199390895), (157247, 0.7530087918754218), (133048, 0.7510742403144018), (51984, 0.748523197644974), (48270, 0.7468234980873414)

In [36]:
import numpy as np

def predict_rating(user_id, item_id, user_movie_matrix, similarities, k=10):
    """
    특정 사용자와 아이템에 대해 평점을 예측.
    
    Parameters:
        user_id (int): 예측할 사용자 ID
        item_id (int): 예측할 아이템 ID
        user_movie_matrix (pd.DataFrame): 사용자-아이템 평점 매트릭스
        similarities (dict): 사용자 간 유사도 딕셔너리
        k (int): 유사한 사용자 수
    
    Returns:
        float: 예측 평점
    """
    # 유사도가 높은 사용자 Top-k 선택
    top_k_users = sorted(similarities.items(), key=lambda x: x[1], reverse=True)[:k]
    
    # 사용자 평균 평점 계산
    user_mean = user_movie_matrix.loc[user_id].mean()
    
    numerator = 0
    denominator = 0
    
    for similar_user, sim in top_k_users:
        if item_id in user_movie_matrix.columns:
            # 유사 사용자의 평균 평점
            similar_user_mean = user_movie_matrix.loc[similar_user].mean()
            
            # 유사 사용자의 평점과 평균 차이
            rating_diff = user_movie_matrix.loc[similar_user, item_id] - similar_user_mean
            
            numerator += sim * rating_diff
            denominator += abs(sim)
    
    # 평점 예측
    if denominator == 0:
        return user_mean  # 유사한 사용자가 없을 경우 평균 평점 반환
    return user_mean + (numerator / denominator)


In [37]:
user_matrix.loc[1.0].mean()

0.0059635486464754755

In [38]:
item_id = "Toy Story"
user_id = 2.0

predicted_rating = predict_rating(user_id, item_id, user_matrix, similarities)
print(f"사용자 {user_id}가 '{item_id}'에 부여할 예측 평점: {predicted_rating:.2f}")

사용자 2.0가 'Toy Story'에 부여할 예측 평점: -0.00


In [40]:
#아이템 기반의 추천 시스템
item_user_matrix = user_matrix.T
item_user_matrix.head()

userId                            1.0       2.0       3.0       4.0       \
original_title                                                             
!Women Art Revolution                  0.0       0.0       0.0       0.0   
$5 a Day                               0.0       0.0       0.0       0.0   
'Gator Bait                            0.0       0.0       0.0       0.0   
'R Xmas                                0.0       0.0       0.0       0.0   
'Twas the Night Before Christmas       0.0       0.0       0.0       0.0   

userId                            5.0       6.0       7.0       8.0       \
original_title                                                             
!Women Art Revolution                  0.0       0.0       0.0       0.0   
$5 a Day                               0.0       0.0       0.0       0.0   
'Gator Bait                            0.0       0.0       0.0       0.0   
'R Xmas                                0.0       0.0       0.0       0.0   
'Twas the Night Before Christmas       0.0       0.0       0.0       0.0   

userId                            9.0       10.0      ...  270887.0  270888.0  \
original_title                                        ...                       
!Women Art Revolution                  0.0       0.0  ...       0.0       0.0   
$5 a Day                               0.0       0.0  ...       0.0       0.0   
'Gator Bait                            0.0       0.0  ...       5.0       0.0   
'R Xmas                                0.0       0.0  ...       0.0       0.0   
'Twas the Night Before Christmas       0.0       0.0  ...       0.0       0.0   

userId                            270889.0  270890.0  270891.0  270892.0  \
original_title                                                             
!Women Art Revolution                  0.0       0.0       0.0       0.0   
$5 a Day                               0.0       0.0       0.0       0.0   
'Gator Bait                            0.0       0.0       0.0       0.0   
'R Xmas                                0.0       0.0       0.0       0.0   
'Twas the Night Before Christmas       0.0       0.0       0.0       0.0   

userId                            270893.0  270894.0  270895.0  270896.0  
original_title                                                            
!Women Art Revolution                  0.0       0.0       0.0       0.0  
$5 a Day                               0.0       0.0       0.0       0.0  
'Gator Bait                            0.0       0.0       0.0       0.0  
'R Xmas                                0.0       0.0       0.0       0.0  
'Twas the Night Before Christmas       0.0       0.0       0.0       0.0  

[5 rows x 265917 columns]

In [42]:
item_similarity = cosine_similarity(item_user_matrix)

# 결과를 데이터프레임으로 변환
item_similarity_df = pd.DataFrame(
    item_similarity, 
    index=item_user_matrix.index, 
    columns=item_user_matrix.index
)
item_similarity_df

original_title                    !Women Art Revolution  $5 a Day  \
original_title                                                      
!Women Art Revolution                          1.000000  0.029322   
$5 a Day                                       0.029322  1.000000   
'Gator Bait                                    0.047221  0.024602   
'R Xmas                                        0.045836  0.049698   
'Twas the Night Before Christmas               0.038059  0.013109   
...                                                 ...       ...   
헬로우 고스트                                        0.247962  0.014549   
형사 Duelist                                     0.013558  0.058919   
활                                              0.012788  0.049724   
회사원                                            0.058860  0.019049   
２０世紀少年< 第1章> 終わりの始まり                           0.017089  0.034561   

original_title                    'Gator Bait   'R Xmas  \
original_title                                            
!Women Art Revolution                0.047221  0.045836   
$5 a Day                             0.024602  0.049698   
'Gator Bait                          1.000000  0.048399   
'R Xmas                              0.048399  1.000000   
'Twas the Night Before Christmas     0.004493  0.034228   
...                                       ...       ...   
헬로우 고스트                              0.078678  0.027866   
형사 Duelist                           0.058149  0.039063   
활                                    0.029215  0.025784   
회사원                                  0.000000  0.017699   
２０世紀少年< 第1章> 終わりの始まり                 0.014692  0.023158   

original_title                    'Twas the Night Before Christmas  (A)Sexual  \
original_title                                                                  
!Women Art Revolution                                     0.038059   0.009036   
$5 a Day                                                  0.013109   0.000000   
'Gator Bait                                               0.004493   0.018743   
'R Xmas                                                   0.034228   0.026588   
'Twas the Night Before Christmas                          1.000000   0.000000   
...                                                            ...        ...   
헬로우 고스트                                                   0.022317   0.012506   
형사 Duelist                                                0.074709   0.000000   
활                                                         0.028325   0.000000   
회사원                                                       0.000000   0.000000   
２０世紀少年< 第1章> 終わりの始まり                                      0.020816   0.000000   

original_title                    ...And the Pursuit of Happiness  \
original_title                                                      
!Women Art Revolution                                    0.072467   
$5 a Day                                                 0.006614   
'Gator Bait                                              0.122750   
'R Xmas                                                  0.018088   
'Twas the Night Before Christmas                         0.022909   
...                                                           ...   
헬로우 고스트                                                  0.096302   
형사 Duelist                                               0.018112   
활                                                        0.006137   
회사원                                                      0.008947   
２０世紀少年< 第1章> 終わりの始まり                                     0.015608   

original_title                    ...Più forte ragazzi!  \
original_title                                            
!Women Art Revolution                          0.092335   
$5 a Day                                       0.039047   
'Gator Bait                                    0.056018   
'R Xmas                                        0.031066   
'Twas the Night Before Chris

In [43]:
def recommend_similar_items(item_title, similarity_matrix, top_n=5):
    """
    특정 아이템과 유사한 아이템 추천
    
    Parameters:
        item_title (str): 기준 아이템 제목
        similarity_matrix (pd.DataFrame): 아이템 간 유사도 행렬
        top_n (int): 추천할 아이템 수
    
    Returns:
        list: 추천 아이템 리스트
    """
    if item_title not in similarity_matrix.index:
        return []
    
    # 아이템 간 유사도 점수 정렬
    similar_items = similarity_matrix[item_title].sort_values(ascending=False)
    
    # 자기 자신 제외하고 Top-N 추천
    recommended_items = similar_items.iloc[1:top_n+1].index.tolist()
    return recommended_items

# 예시: "Toy Story"와 유사한 영화 추천
recommended_items = recommend_similar_items("Toy Story", item_similarity_df, top_n=5)
print("추천 아이템:", recommended_items)


추천 아이템: ['Born into Brothels', 'WarGames', 'Nuit et brouillard', 'The Wizard of Oz', 'Amores perros']


In [52]:
def predict_item_rating(user_id, item_title, user_item_matrix, similarity_matrix, top_n=5):
    """
    특정 사용자와 아이템에 대해 평점을 예측
    
    Parameters:
        user_id (int): 사용자 ID
        item_title (str): 아이템 제목
        user_item_matrix (pd.DataFrame): 사용자-아이템 매트릭스
        similarity_matrix (pd.DataFrame): 아이템 간 유사도 행렬
        top_n (int): 유사한 아이템 수
    
    Returns:
        float: 예측 평점
    """
    if item_title not in similarity_matrix.index or user_id not in user_item_matrix.index:
        return 0
    
    # 유사한 아이템 선택
    similar_items = similarity_matrix[item_title].sort_values(ascending=False)
    similar_items = similar_items.iloc[1:top_n+1]
    
    # 예측 평점 계산
    numerator = 0
    denominator = 0
    print(similar_items)
    for similar_item, sim in similar_items.items():
        if similar_item in user_item_matrix.columns:
            rating = user_item_matrix.loc[user_id, similar_item]
            print('rating', rating)
            numerator += sim * rating
            denominator += abs(sim)
    
    return numerator / denominator if denominator != 0 else 0

# 예시: 사용자 1923이 "Toy Story"의 평점을 예측
predicted_rating = predict_item_rating(3.0, "Toy Story", user_matrix, item_similarity_df)
print(f"예측 평점: {predicted_rating:.2f}")


original_title
Born into Brothels    0.152207
WarGames              0.150745
Nuit et brouillard    0.142920
The Wizard of Oz      0.138688
Amores perros         0.133954
Name: Toy Story, dtype: float64
rating 0.0
rating 0.0
rating 0.0
rating 0.0
rating 0.0
예측 평점: 0.00


In [61]:
user_matrix.loc[3,['Born into Brothels','WarGames' ,'Nuit et brouillard','The Wizard of Oz','Amores perros']]

original_title
Born into Brothels    0.0
WarGames              0.0
Nuit et brouillard    0.0
The Wizard of Oz      0.0
Amores perros         0.0
Name: 3.0, dtype: float64

original_title
!Women Art Revolution               0.0
$5 a Day                            0.0
'Gator Bait                         0.0
'R Xmas                             0.0
'Twas the Night Before Christmas    0.0
                                   ... 
헬로우 고스트                             0.0
형사 Duelist                          0.0
활                                   0.0
회사원                                 0.0
２０世紀少年< 第1章> 終わりの始まり                0.0
Name: 2.0, Length: 7462, dtype: float64

In [64]:
movie_ratings_small.head()
movie_ratings_small.shape

(100004, 4)

In [65]:
movie_ratings.shape

(26024289, 4)